In [40]:
# Imports
import glob
import pandas as pd
from bs4 import BeautifulSoup
import json

In [41]:
# Constants, variables and important data

ROOT = "/Users/hagenaadfock/Downloads/BBC/*"
folders = glob.glob(ROOT)

files = []

for folder in folders:
    files.append(glob.glob(f'{folder}/*.html'))
files = [item for sublist in files for item in sublist]

In [42]:
def extract_data(files):
    data = []
    fucked_websites = 0
    for index, file in enumerate(files):
        if './data/show' not in file:
            try:
                soup = BeautifulSoup(open(file), 'html.parser')
            except Exception as error:
                print(error)
                fucked_websites = fucked_websites + 1
                continue
            print(file)

            if soup.find('meta', attrs={'property': 'og:description'}):
                description = soup.find('meta', attrs={'property': 'og:description'})['content']
            else:
                description = ''

            if soup.find('meta', attrs={'name': 'keywords'}):
                keywords = soup.find('meta', attrs={'name': 'keywords'})['content']
            else:
                keywords = ''

            # Extract Json
            if soup.find(id="tvip-script-app-store"):
                json_raw = soup.find(id="tvip-script-app-store")
                json_raw = json_raw.get_text()
                json_raw = json_raw.partition("__IPLAYER_REDUX_STATE__ = ")
                stripped_text = json_raw[2][:len(json_raw[2]) - 1]
                jsonfile = json.loads(stripped_text)


                episode_ = jsonfile['episode']
                title = episode_['title']

                synopses_ = episode_['synopses']
                if 'large' in synopses_:
                    synops_long = synopses_['large']
                else:
                    synops_long = ''
                if 'medium' in synopses_:
                    synops_med = synopses_['medium']
                else:
                    synops_med = ''
                if 'small' in synopses_:
                    synops_small = synopses_['small']
                else:
                    synops_small = ''

                if 'images' in episode_:
                    image = episode_['images']
                    if 'promotional' in image:
                        image = image['promotional_with_logo']
                    elif 'promotional' in image:
                        image = image['promotional_with_logo']
                    else:
                        image = image['standard']
                else:
                    image = ''

                if 'subtitle' in episode_:
                    subtitle = episode_['subtitle']
                else:
                    subtitle = ''

                category = ''
                if 'labels' in episode_:
                    labels_ = episode_['labels']
                    if 'category' in labels_:
                        category = labels_['category']

                channel = episode_['masterBrand']['id']
                versions_ = jsonfile['versions'][0]
                language = versions_['guidance']
                if 'firstBroadcast' in versions_:
                    release_date = versions_['firstBroadcast']
                else:
                    release_date = ''
                duration_sec = versions_['duration']['seconds']
            else:
                title = ''
                synops_long = ''
                synops_med = ''
                synops_small = ''
                category = ''
                channel = ''
                language = ''
                release_date = ''
                duration_sec = ''
                image = ''

            article = {
                'id': index,
                'title': title,
                'subtitle': subtitle,
                'description': description,
                'image': image,
                'keywords': keywords,
                'synopses_small': synops_small,
                'synops_med': synops_med,
                'synops_long': synops_long,
                'category': category,
                'channel': channel,
                'language': language,
                'release_date': release_date,
                'duration_sec': duration_sec,
                'topic': file.split('/',6)[5]
            }
            # append the article to the data
            data.append(article)

    print(f'In total {fucked_websites} were fucked')
    return data

In [43]:
# load html files
data = extract_data(files)

/Users/hagenaadfock/Downloads/BBC/music/iplayer-episode-m00110rn-the-80s-musics-greatest-decade-series-1-1-with-dylan-jones.html
/Users/hagenaadfock/Downloads/BBC/music/iplayer-episode-m0014zvn-top-of-the-pops-02071992.html
/Users/hagenaadfock/Downloads/BBC/music/iplayer-episode-m000zp6r-bbc-proms-2021-last-night-of-the-proms-part-2.html
/Users/hagenaadfock/Downloads/BBC/music/iplayer-episode-m000kqv6-port-series-5-episode-4.html
/Users/hagenaadfock/Downloads/BBC/music/iplayer-episode-p0bn4w25-sit-down-stand-up-with-greg-james.html
/Users/hagenaadfock/Downloads/BBC/music/iplayer-episode-m0009914-pop-goes-northern-ireland-series-5-3-1978.html
/Users/hagenaadfock/Downloads/BBC/music/iplayer-episode-m000x296-bbc-cardiff-singer-of-the-world-2021-round-2.html
/Users/hagenaadfock/Downloads/BBC/music/iplayer-episode-m0008zbs-the-live-lounge-show-series-3-1-with-taylor-swift.html
/Users/hagenaadfock/Downloads/BBC/music/iplayer-episode-b0956jf9-the-live-lounge-show-series-1-1-foo-fighters-and-m

In [44]:
data

[{'id': 0,
  'title': 'The 80s - Music’s Greatest Decade?',
  'subtitle': 'Series 1: 1. With Dylan Jones',
  'description': 'Music author Dylan Jones argues that the 1980s were the most innovative decade in pop.',
  'image': 'https://ichef.bbci.co.uk/images/ic/{recipe}/p09z8fjg.jpg',
  'keywords': 'BBC, iPlayer, TV, The 80s - Music’s Greatest Decade?, Series 1: 1. With Dylan Jones',
  'synopses_small': 'Music author Dylan Jones argues that the 1980s were the most innovative decade in pop.',
  'synops_med': 'Music writer Dylan Jones puts the case that the 1980s were the most radical, innovative and creative decade in the history of pop.',
  'synops_long': 'Eighties music is often dismissed as a joke - all drum machines and big hair. But - as acclaimed author Dylan Jones argues in this film – the 1980s should be looked on as the most creative, radical and innovative decade in pop.\n \nThis was the decade when the world-conquering genres of rap, hip-hop and modern dance music were launche

In [45]:
df = pd.DataFrame.from_records(data, index='id')

In [46]:
df.to_csv('./bbc_data_raw.csv', sep=';')

In [47]:
df

title  \
id                                          
0      The 80s - Music’s Greatest Decade?   
1                         Top of the Pops   
2                               BBC Proms   
3                                    Port   
4      Sit Down, Stand Up with Greg James   
...                                   ...   
36896                      Justin's House   
36897              Number 1 Newton Avenue   
36898                           Biggleton   
36899                          Go Jetters   
36900                Oti's Boogie Beebies   

                                         subtitle  \
id                                                  
0                   Series 1: 1. With Dylan Jones   
1                                      02/07/1992   
2           2021: Last Night of the Proms, Part 2   
3                             Series 5: Episode 4   
4                                                   
...                                           ...   
36896                 Series 2: 4. Going for Gold   
36897                          Series 1: 21. Goal   
36898                   Series 2: 23. Big Day Out   
36899  Series 1: 27. The Strokkur Geyser, Iceland   
36900                   Series 1: 12. Upside Down   

                                             description  \
id                                                         
0      Music author Dylan Jones argues that the 1980s...   
1      With Arrested Development, Altern 8, Def Leppa...   
2      Australian tenor Stuart Skelton is joined by L...   
3      Previously unseen music from the series Port, ...   
4      Tom Holland and Greg James cold call celebrity...   
...                                                  ...   
36896  Justin's house hosts the Justinship Games, and...   
36897  It’s all about measuring today when Libby play...   
36898  Odd Job Laila has lots of jobs to do around to...   
36899  The geysers in Iceland are blocked and Glitch ...   
36900  In this episode, Oti teaches us how to step an...   

                                                   image  \
id                                                         
0      https://ichef.bbci.co.uk/images/ic/{recipe}/p0...   
1      https://ichef.bbci.co.uk/images/ic/{recipe}/p0...   
2      https://ichef.bbci.co.uk/images/ic/{recipe}/p0...   
3      https://ichef.bbci.co.uk/images/ic/{recipe}/p0...   
4      https://ichef.bbci.co.uk/images/ic/{recipe}/p0...   
...                                                  ...   
36896  https://ichef.bbci.co.uk/images/ic/{recipe}/p0...   
36897  https://ichef.bbci.co.uk/images/ic/{recipe}/p0...   
36898  https://ichef.bbci.co.uk/images/ic/{recipe}/p0...   
36899  https://ichef.bbci.co.uk/images/ic/{recipe}/p0...   
36900  https://ichef.bbci.co.uk/images/ic/{recipe}/p0...   

                                                keywords  \
id                                                         
0      BBC, iPlayer, TV, The 80s - Music’s Greatest D...   
1          BBC, iPlayer, TV, Top of the Pops, 02/07/1992   
2      BBC, iPlayer, TV, BBC Proms, 2021: Last Night ...   
3            BBC, iPlayer, TV, Port, Series 5: Episode 4   
4      BBC, iPlayer, TV, Sit Down, Stand Up with Greg...   
...                                                  ...   
36896  BBC, iPlayer, TV, Justins House, Series 2: 4. ...   
36897  BBC, iPlayer, TV, Number 1 Newton Avenue, Seri...   
36898  BBC, iPlayer, TV, Biggleton, Series 2: 23. Big...   
36899  BBC, iPlayer, TV, Go Jetters, Series 1: 27. Th...   
36900  BBC, iPlayer, TV, Otis Boogie Beebies, Series ...   

                                          synopses_small  \
id                                                         
0      Music author Dylan Jones argues that the 1980s...   
1      With Arrested Development, Altern 8, Def Leppa...   
2      Australian tenor Stuart Skelton is joined by L...   
3      Previously unseen music from the series Port, ...   
4      Tom Holland and Greg James cold call celebrity... 